In [1]:
import geopandas as gpd
import folium
from shapely.geometry import Polygon, Point
import pandas as pd
import numpy as np 

In [4]:
zone = gpd.read_file('https://storageaccount11111111.blob.core.windows.net/container1/Leuven/socio_demographic_data/leuven_statsec.gpkg')
zone = zone.to_crs('epsg:4326')
zone.reset_index(inplace=True)

zone.head(3)

index   UIDN  OIDN     CODSEC NISCODE   SEC           SECNAAM   LENGTE  \
0      0  19880  4074  24062A61-   24062  A61-        KAREELVELD  5896.98   
1      1  20055  4078  24062B100   24062  B100  PUTKAPEL-CENTRUM  5277.17   
2      2  20056  4087  24062B34-   24062  B34-        ROESELBERG  4205.81   

      OPPERVL            STDEEL  \
0  1529378.12      LEUVEN NOORD   
1   980502.76  WILSELE WIJGMAAL   
2   643689.23  WILSELE WIJGMAAL   

                                            geometry  
0  MULTIPOLYGON (((4.68850 50.89458, 4.68895 50.8...  
1  MULTIPOLYGON (((4.72796 50.93378, 4.72742 50.9...  
2  MULTIPOLYGON (((4.69867 50.89670, 4.69866 50.8...

In [5]:
def style(fill_color, border_color, spessore_contorno=2, opacita=0.5):
    return {
        'fillColor': fill_color,
        'color': border_color,
        'weight': spessore_contorno,
        'fillOpacity': opacita
    }

In [7]:
from routingpy.routers import MapboxOSRM
MY_MAPBOXOSRM_API_KEY = 'pk.eyJ1IjoidnBpYyIsImEiOiJjbHI3aXQ5Mm0yOWlkMmpudnBtNHJ5OGx0In0.yXnhEOyVnjz6nriA4GK2-g'
mb = MapboxOSRM(api_key = MY_MAPBOXOSRM_API_KEY)

def mb_isochrone(gdf, time, profile = "driving"):

    gdf['LON_VALUE'] = gdf.to_crs(4326).geometry.x
    gdf['LAT_VALUE'] = gdf.to_crs(4326).geometry.y

    coordinates = gdf[['LON_VALUE', 'LAT_VALUE']].values.tolist()

    isochrone_shapes = []

    if type(time) is not list:
        time = [time]

    time_seconds = [60 * x for x in time]

    # Given the way that routingpy works, we need to iterate through the list of 
    # coordinate pairs, then iterate through the object returned and extract the 
    # isochrone geometries.  
    for c in coordinates:
        iso_request = mb.isochrones(locations = c, profile = profile,
                                    intervals = time_seconds, polygons = "true")
        #print('iso request:', iso_request)
        for i in iso_request:
            iso_geom = Polygon(i.geometry[0])
            isochrone_shapes.append(iso_geom)

    # re-build the dataset but with isochrone geometries
    df_values = gdf.drop(columns = ['geometry', 'LON_VALUE', 'LAT_VALUE'])

    time_col = time * len(df_values)

    # need to repeat the dataframe to account for multiple time intervals
    df_values_rep = pd.DataFrame(np.repeat(df_values.values, len(time_seconds), axis = 0))
    df_values_rep.columns = df_values.columns

    isochrone_gdf = gpd.GeoDataFrame(
        data = df_values_rep,
        geometry = isochrone_shapes,
        crs = 4326
    )

    isochrone_gdf['time'] = time_col

    # sorting the dataframe in descending order of time to improve visualization
    # (the smallest isochrones should go on top, which means they are plotted last)
    isochrone_gdf = isochrone_gdf.sort_values('time', ascending = False)

    return(isochrone_gdf)

In [17]:
station = (4.714594, 50.882175)

start_time_intervals = [5, 10, 15]  

hub_locations = [station]
geometry = [Point(station)]
gdf = gpd.GeoDataFrame(geometry=gpd.GeoSeries(geometry), crs="EPSG:4326")

isochrone_data = {}

for hub_location in hub_locations:
    for time_interval in start_time_intervals:
        isochrone_data[(hub_location, time_interval)] = mb_isochrone(gdf, time_interval, profile="cycling")

gdf_list = [gdff.reset_index(drop=True) for gdff in isochrone_data.values()]
gdf_isoc = gpd.GeoDataFrame(pd.concat(gdf_list, keys=isochrone_data.keys(), names=['geo', 'tempi']))
gdf_isoc.reset_index(inplace=True)
coordinates_list = list(gdf_isoc['geometry'][2].exterior.coords)

points_gdf = gpd.GeoDataFrame(geometry=[Point(lon, lat) for lon, lat in coordinates_list], crs=gdf.crs)


central_point_coords = zone.unary_union.centroid.x, zone.unary_union.centroid.y
central_point = Point(central_point_coords)

mappa = folium.Map(location = (central_point_coords[1], central_point_coords[0]), zoom_start = 12.5) 

for index, row in points_gdf.iterrows():
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='yellow',
        fill=True,
        fill_color='yellow'
    ).add_to(mappa)

# Display the map
mappa

In [18]:
##PRUNING 

def remove_neighbors(gdf, current_id, radius):
    current_point = gdf.loc[gdf['ID'] == current_id, 'geometry'].iloc[0]
    neighbors = gdf.loc[gdf['geometry'].distance(current_point) < radius, 'ID'].tolist()
    neighbors.remove(current_id)  
    return neighbors

radius = 0.002
points_gdf_pruned = points_gdf.copy()
points_gdf_pruned['ID'] = range(len(points_gdf_pruned))
indices_to_remove = []
for current_id, row in points_gdf_pruned.iterrows():
    # print('current ID:', current_id)
    neighbors = remove_neighbors(points_gdf_pruned, current_id, radius)
    indices_to_remove.extend(neighbors)

points_gdf_pruned= points_gdf_pruned.drop(indices_to_remove)

print('pre:', len(points_gdf))
print('post:', len(points_gdf_pruned))


C:\Users\Valeria\AppData\Local\Temp\ipykernel_11332\3129601325.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  neighbors = gdf.loc[gdf['geometry'].distance(current_point) < radius, 'ID'].tolist()


pre: 320
post: 22


In [19]:
for index, row in points_gdf_pruned.iterrows():
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='green',
        fill=True,
        fill_color='green'
    ).add_to(mappa)

mappa

In [20]:
### SECONDA 
isocrone_seconda = mb_isochrone(points_gdf_pruned, time=15, profile="cycling")
exterior_coords_list = []
for index, row in isocrone_seconda.iterrows():
    exterior_coords = list(row['geometry'].exterior.coords)
    exterior_coords_list.append(exterior_coords)

boundary = zone.unary_union
boundary_gdf = gpd.GeoDataFrame(geometry=[boundary], crs="EPSG:4326")
# mi tengo solo i punti che ricadono nel boundary che ho definito prima 
filtered_exterior_coords_list = []
for exterior_coords in exterior_coords_list:
    filtered_exterior_coords = [coord for coord in exterior_coords if Point(coord).within(boundary)]
    filtered_exterior_coords_list.append(filtered_exterior_coords)

# aggiungo questi punti alla mappa (candidate hubs), sono i red dots 
for exterior_coords in filtered_exterior_coords_list:
    for coord in exterior_coords:
        folium.CircleMarker(location=[coord[1], coord[0]], radius=3, color='red', fill=True, fill_color='red').add_to(mappa)
mappa

In [24]:
##PRUNING 
flat_coordinates_list = [coord for sublist in filtered_exterior_coords_list for coord in sublist]
points_gdf_seconda = gpd.GeoDataFrame(geometry=[Point(lon, lat) for lon, lat in flat_coordinates_list], crs="EPSG:4326")


def remove_neighbors(gdf, current_id, radius):
    current_point = gdf.loc[gdf['ID'] == current_id, 'geometry'].iloc[0]
    neighbors = gdf.loc[gdf['geometry'].distance(current_point) < radius, 'ID'].tolist()
    neighbors.remove(current_id)  
    return neighbors

radius = 0.002
points_gdf_seconda_pruned = points_gdf_seconda.copy()
points_gdf_seconda_pruned['ID'] = range(len(points_gdf_seconda_pruned))
indices_to_remove = []
for current_id, row in points_gdf_seconda_pruned.iterrows():
    # print('current ID:', current_id)
    neighbors = remove_neighbors(points_gdf_seconda_pruned, current_id, radius)
    indices_to_remove.extend(neighbors)

points_gdf_seconda_pruned= points_gdf_seconda_pruned.drop(indices_to_remove)

print('pre:', len(points_gdf_seconda))
print('post:', len(points_gdf_seconda_pruned))


C:\Users\Valeria\AppData\Local\Temp\ipykernel_11332\557115944.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  neighbors = gdf.loc[gdf['geometry'].distance(current_point) < radius, 'ID'].tolist()


pre: 3657
post: 32


In [25]:
for index, row in points_gdf_seconda_pruned.iterrows():
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='purple',
        fill=True,
        fill_color='purple'
    ).add_to(mappa)

mappa

In [ ]:
mappa_nuova = folium.Map(location = (central_point_coords[1], central_point_coords[0]), zoom_start = 12.5) 

for index, row in points_gdf_pruned.iterrows(): #prima corona 
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='green',
        fill=True,
        fill_color='green'
    ).add_to(mappa_nuova)

for index, row in points_gdf_seconda_pruned.iterrows(): #seconda corona 
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='purple',
        fill=True,
        fill_color='purple'
    ).add_to(mappa_nuova)


In [29]:
folium.GeoJson(boundary_gdf, style_function = lambda x: style('purple', 'purple', spessore_contorno = 3, opacita = 0.01)).add_to(mappa_nuova)
mappa_nuova

In [30]:
#### TERZA 

isocrone_terza = mb_isochrone(points_gdf_seconda_pruned, time=15, profile="cycling")
exterior_coords_list = []
for index, row in isocrone_terza.iterrows():
    exterior_coords = list(row['geometry'].exterior.coords)
    exterior_coords_list.append(exterior_coords)

# mi tengo solo i punti che ricadono nel boundary che ho definito prima 
filtered_exterior_coords_list = []
for exterior_coords in exterior_coords_list:
    filtered_exterior_coords = [coord for coord in exterior_coords if Point(coord).within(boundary)]
    filtered_exterior_coords_list.append(filtered_exterior_coords)


### PRUNING TERZA

flat_coordinates_list = [coord for sublist in filtered_exterior_coords_list for coord in sublist]
points_gdf_terza = gpd.GeoDataFrame(geometry=[Point(lon, lat) for lon, lat in flat_coordinates_list], crs="EPSG:4326")
points_gdf_terza_pruned = points_gdf_terza.copy()
points_gdf_terza_pruned['ID'] = range(len(points_gdf_terza_pruned))
indices_to_remove = []
for current_id, row in points_gdf_terza_pruned.iterrows():
    # print('current ID:', current_id)
    neighbors = remove_neighbors(points_gdf_terza_pruned, current_id, radius)
    indices_to_remove.extend(neighbors)

points_gdf_terza_pruned= points_gdf_terza_pruned.drop(indices_to_remove)

print('pre:', len(points_gdf_terza))
print('post:', len(points_gdf_terza_pruned))


# VIZ

mappa_nuova = folium.Map(location = (central_point_coords[1], central_point_coords[0]), zoom_start = 12.5) 

for index, row in points_gdf_pruned.iterrows(): #prima corona 
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='green',
        fill=True,
        fill_color='green'
    ).add_to(mappa_nuova)

for index, row in points_gdf_seconda_pruned.iterrows(): #seconda corona 
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='purple',
        fill=True,
        fill_color='purple'
    ).add_to(mappa_nuova)

for index, row in points_gdf_terza_pruned.iterrows(): #terza corona 
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='red',
        fill=True,
        fill_color='red'
    ).add_to(mappa_nuova)

mappa_nuova

C:\Users\Valeria\AppData\Local\Temp\ipykernel_11332\557115944.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  neighbors = gdf.loc[gdf['geometry'].distance(current_point) < radius, 'ID'].tolist()


pre: 4466
post: 10


In [34]:
#### QUARTA

isocrone_quarta = mb_isochrone(points_gdf_terza_pruned, time=15, profile="cycling")
exterior_coords_list = []
for index, row in isocrone_quarta.iterrows():
    exterior_coords = list(row['geometry'].exterior.coords)
    exterior_coords_list.append(exterior_coords)

# mi tengo solo i punti che ricadono nel boundary che ho definito prima 
filtered_exterior_coords_list = []
for exterior_coords in exterior_coords_list:
    filtered_exterior_coords = [coord for coord in exterior_coords if Point(coord).within(boundary)]
    filtered_exterior_coords_list.append(filtered_exterior_coords)


### PRUNING QUARTA

flat_coordinates_list = [coord for sublist in filtered_exterior_coords_list for coord in sublist]
points_gdf_quarta = gpd.GeoDataFrame(geometry=[Point(lon, lat) for lon, lat in flat_coordinates_list], crs="EPSG:4326")
points_gdf_quarta_pruned = points_gdf_quarta.copy()
points_gdf_quarta_pruned['ID'] = range(len(points_gdf_quarta_pruned))
indices_to_remove = []
for current_id, row in points_gdf_quarta_pruned.iterrows():
    # print('current ID:', current_id)
    neighbors = remove_neighbors(points_gdf_quarta_pruned, current_id, radius)
    indices_to_remove.extend(neighbors)

points_gdf_quarta_pruned= points_gdf_quarta_pruned.drop(indices_to_remove)

print('pre:', len(points_gdf_quarta))
print('post:', len(points_gdf_quarta_pruned))


# VIZ

mappa_nuova = folium.Map(location = (central_point_coords[1], central_point_coords[0]), zoom_start = 12.5) 

for index, row in points_gdf_pruned.iterrows(): #prima corona 
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='green',
        fill=True,
        fill_color='green'
    ).add_to(mappa_nuova)

for index, row in points_gdf_seconda_pruned.iterrows(): #seconda corona 
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='purple',
        fill=True,
        fill_color='purple'
    ).add_to(mappa_nuova)

for index, row in points_gdf_terza_pruned.iterrows(): #terza corona 
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='red',
        fill=True,
        fill_color='red'
    ).add_to(mappa_nuova)


for index, row in points_gdf_quarta_pruned.iterrows(): #quarta corona 
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='blue',
        fill=True,
        fill_color='blue'
    ).add_to(mappa_nuova)

folium.GeoJson(boundary_gdf, style_function = lambda x: style('purple', 'purple', spessore_contorno = 3, opacita = 0.01)).add_to(mappa_nuova)   
mappa_nuova

C:\Users\Valeria\AppData\Local\Temp\ipykernel_11332\557115944.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  neighbors = gdf.loc[gdf['geometry'].distance(current_point) < radius, 'ID'].tolist()


pre: 1278
post: 36


In [35]:
### QUINTA
isocrone_quinta = mb_isochrone(points_gdf_quarta_pruned, time=15, profile="cycling")
exterior_coords_list = []
for index, row in isocrone_quinta.iterrows():
    exterior_coords = list(row['geometry'].exterior.coords)
    exterior_coords_list.append(exterior_coords)

# mi tengo solo i punti che ricadono nel boundary che ho definito prima 
filtered_exterior_coords_list = []
for exterior_coords in exterior_coords_list:
    filtered_exterior_coords = [coord for coord in exterior_coords if Point(coord).within(boundary)]
    filtered_exterior_coords_list.append(filtered_exterior_coords)


### PRUNING QUINTA

flat_coordinates_list = [coord for sublist in filtered_exterior_coords_list for coord in sublist]
points_gdf_quinta = gpd.GeoDataFrame(geometry=[Point(lon, lat) for lon, lat in flat_coordinates_list], crs="EPSG:4326")
points_gdf_quinta_pruned = points_gdf_quinta.copy()
points_gdf_quinta_pruned['ID'] = range(len(points_gdf_quinta_pruned))
indices_to_remove = []
for current_id, row in points_gdf_quinta_pruned.iterrows():
    # print('current ID:', current_id)
    neighbors = remove_neighbors(points_gdf_quinta_pruned, current_id, radius)
    indices_to_remove.extend(neighbors)

points_gdf_quinta_pruned= points_gdf_quinta_pruned.drop(indices_to_remove)

print('pre:', len(points_gdf_quinta))
print('post:', len(points_gdf_quinta_pruned))


# VIZ

mappa_nuova = folium.Map(location = (central_point_coords[1], central_point_coords[0]), zoom_start = 12.5) 

for index, row in points_gdf_pruned.iterrows(): #prima corona 
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='green',
        fill=True,
        fill_color='green'
    ).add_to(mappa_nuova)

for index, row in points_gdf_seconda_pruned.iterrows(): #seconda corona 
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='purple',
        fill=True,
        fill_color='purple'
    ).add_to(mappa_nuova)

for index, row in points_gdf_terza_pruned.iterrows(): #terza corona 
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='red',
        fill=True,
        fill_color='red'
    ).add_to(mappa_nuova)


for index, row in points_gdf_quarta_pruned.iterrows(): #quarta corona 
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='blue',
        fill=True,
        fill_color='blue'
    ).add_to(mappa_nuova)

for index, row in points_gdf_quinta_pruned.iterrows(): #quinta corona 
    folium.CircleMarker(
        location=[row['geometry'].y, row['geometry'].x],
        radius=3,
        color='yellow',
        fill=True,
        fill_color='yellow'
    ).add_to(mappa_nuova)

folium.GeoJson(boundary_gdf, style_function = lambda x: style('purple', 'purple', spessore_contorno = 3, opacita = 0.01)).add_to(mappa_nuova)   
mappa_nuova

C:\Users\Valeria\AppData\Local\Temp\ipykernel_11332\557115944.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  neighbors = gdf.loc[gdf['geometry'].distance(current_point) < radius, 'ID'].tolist()
